# Mathematical Modeling Project Work
### Tamás Gyenis 2023 January

## 1. Introduction
This notebook aims to present the data exploration and modeling process for a public Kaggle dataset, <a href="https://www.kaggle.com/datasets/jacklacey/left-4-dead-2-20000-player-stats">*Left 4 Dead 2 20,000+ Player's Statistics*</a>. The dataset has more than 20k records of player's performances and behaviour in a shooting type video game. The data was collected from public sources and stored in a structured relational database, saved in a csv file. In this project I try to predict how much time a player has spent playing the game from their in-game performance. Also, I try to estimate which difficulty is set for a player based on the same features. I chose both a regression and a classification task to have the opportunity to practice both of those modeling types. The goal is to get better performance than naive regression and classification models. We have to mention, that no previous modeling has been done on the dataset, so achievable model performances are unknown.

## 2. Feature Extraction
In order to be able to analyze the dataset better and prepare it for modeling, we need some feature engineering first. In this section I describe the available features and I also construct some potentially useful ones.

In [69]:
import pandas as pd
import plotly.express as px

In [70]:
# we use plotly, for easier documentation later: I can zoom, crop etc. Some styling.
px.defaults.template = 'plotly_dark'
px.defaults.width = 800
px.defaults.height = 450

In [71]:
# load data
raw_data_path = 'C:/Dev/ELTE_AI/mat_mod/data/l4d2_player_stats_final.csv'

# I like to save an original copy of the dataset before any modification, so we can retrieve information more easily
df_original = pd.read_csv(raw_data_path)
df = df_original.copy(deep=True)

In [72]:
df.head(5)

Username  Playtime_(Hours)  Pistol_Shots  Pistol_Kills  Pistol_Usage  \
0         0       2433.577222       94665.0       10470.0          2.77   
1         1        121.879444        9136.0        1371.0          1.47   
2         2         69.955278        4100.0         693.0          4.87   
3         3         48.421667        7369.0        1208.0          5.99   
4         4        307.639722       51944.0        9481.0          8.93   

   Magnum_Shots  Magnum_Kills  Magnum_Usage  Uzi_Shots  Uzi_Kills  ...  \
0      121222.0       27056.0          7.16    44666.0     5165.0  ...   
1       14928.0        6802.0          7.30      997.0      187.0  ...   
2         222.0         133.0          0.93     2834.0      271.0  ...   
3         784.0         250.0          1.24     3322.0      496.0  ...   
4       20545.0        6813.0          6.42    38224.0     5493.0  ...   

   Knife_Usage  Molotovs_Thrown  Molotov_Kills  Pipe_Bombs_Thrown  \
0         0.47          11166.0        99278.0             5817.0   
1         0.03            788.0        10141.0              977.0   
2         0.00             23.0          130.0              445.0   
3         0.00            135.0         1090.0              105.0   
4         0.00            613.0         4797.0              515.0   

   Pipe_Bomb_Kills  Bile_Jars_Thrown  Bile_Jar_Hits  Most_Friendly_Fire  \
0          23433.0            5802.0        12863.0             13653.0   
1           6962.0             519.0         1557.0              1914.0   
2           1202.0              44.0           83.0              3195.0   
3            716.0              48.0           75.0              1412.0   
4           4195.0             272.0          424.0             10851.0   

   Difficulty  Average_Friendly_Fire  
0      Normal                  142.0  
1      Expert                   89.0  
2      Expert                   58.0  
3      Expert                   76.0  
4      Expert                  112.0  

[5 rows x 113 columns]

Let's convert column names to camel case. Also, we should convert the only string column 'Difficulty' to numerical.

In [73]:
# convert column names to snake case
df.rename(columns={col: col.lower() for col in df.columns}, inplace=True)
df.rename(columns={'playtime_(hours)': 'playtime'}, inplace=True)

# convert difficulty from string to numeric
difficulty_map = {'Easy': 0,
                  'Normal': 1,
                  'Advanced': 2,
                  'Expert': 3}

df['difficulty'] = df['difficulty'].map(difficulty_map)

In [74]:
df.describe()

username       playtime   pistol_shots   pistol_kills  \
count  20830.000000   20830.000000   20830.000000   20830.000000   
mean   10414.500000     104.684003   12389.739558    2031.092127   
std     6013.247389    1974.873029   24198.764272    3944.710074   
min        0.000000       0.000000       0.000000       0.000000   
25%     5207.250000      19.027153    3336.500000     519.000000   
50%    10414.500000      36.110417    6568.000000    1060.000000   
75%    15621.750000      73.698333   12966.750000    2153.000000   
max    20829.000000  277827.960278  608711.000000  131565.000000   

       pistol_usage   magnum_shots   magnum_kills  magnum_usage  \
count  20830.000000   20830.000000   20830.000000  20830.000000   
mean       8.035493    4948.215218    1984.546471      5.151902   
std        6.324443   16679.459523    8250.642273      5.586247   
min        0.000000       0.000000       0.000000      0.000000   
25%        4.800000     522.000000     164.000000      1.580000   
50%        6.680000    1462.000000     502.000000      3.540000   
75%        9.470000    3918.000000    1446.000000      6.807500   
max      100.000000  627966.000000  411640.000000    100.000000   

           uzi_shots      uzi_kills  ...   knife_usage  molotovs_thrown  \
count   20830.000000   20830.000000  ...  20830.000000     20830.000000   
mean     7227.586990    1274.591119  ...      0.050348       248.814546   
std     20501.115475    3779.680779  ...      0.302169      1333.472437   
min         0.000000       0.000000  ...      0.000000         0.000000   
25%      1204.000000     195.000000  ...      0.000000        33.000000   
50%      2923.500000     506.000000  ...      0.000000        75.000000   
75%      6364.250000    1146.750000  ...      0.000000       175.000000   
max    731767.000000  152921.000000  ...     21.320000    125856.000000   

       molotov_kills  pipe_bombs_thrown  pipe_bomb_kills  bile_jars_thrown  \
count   20830.000000       20830.000000     20830.000000      20830.000000   
mean     2000.592751         255.532117      1799.752184        120.713778   
std     10028.704910         924.607365      6059.289202        586.911986   
min         0.000000           0.000000         0.000000          0.000000   
25%       237.000000          43.000000       286.000000         15.000000   
50%       583.000000          95.000000       658.000000         36.000000   
75%      1388.750000         210.750000      1457.000000         86.000000   
max    635486.000000       55566.000000    249158.000000      41774.000000   

       bile_jar_hits  most_friendly_fire    difficulty  average_friendly_fire  
count   20830.000000        2.083000e+04  20830.000000           20830.000000  
mean      179.056313        4.976528e+04      1.773932              81.363946  
std       873.542727        6.928768e+06      1.007877             879.579826  
min         0.000000        0.000000e+00      0.000000               0.000000  
25%        22.000000        3.010000e+02      1.000000              35.000000  
50%        58.000000        7.050000e+02      2.000000              55.000000  
75%       137.000000        1.441000e+03      3.000000              88.000000  
max     87673.000000        1.000000e+09      3.000000          121347.000000  

[8 rows x 113 columns]

We can see that most of the 113 columns are very similar: player statistic with a given weapon. The *usage* is a ratio of how much a weapon is being used by a player during playtime. The *shots* describe the number of trigger pulls with the weapon and the *kills* the number of successfully takedowns. The weapons though, can be separated to two categories: actual weapons that the player can equip and use, like *uzi* or *knife* and utility weapons that can be thrown like *molotov* or *bile_jar*. We should treat these features differently. Also, there are some columns that don't describe weapon performances like *average_friendly_fire*, *playtime* or *username*. These will be called meta columns. Now let's separate the different feature types and the columns belonging to them.

In [75]:
weapon_names = [col.split('_shots')[0] for col in df.columns if 'shots' in col]
utility_names = [utility_name.split('_thrown')[0] for utility_name in df.columns if 'thrown' in utility_name]
meta_names = ['username', 'playtime', 'difficulty', 'average_friendly_fire']

In [77]:
# pltiing the sum usage of weapons
sum_weapon_usage = df[[col for col in df.columns if 'usage' in col]].sum(axis=0).sort_values(ascending=False)
px.bar(sum_weapon_usage).update_layout(
    xaxis_title='weapon', yaxis_title='sum usage', title='usage of different weapons')

If we plot the sum of usages of all the samples for the different weapons we can see which are the most popular ones. Also, we can see that some weapons are hardly used. After checking why, I found out that these were added to the game later, so players didn't have a chance to use them. We should exclude these from the dataset.

In [85]:
weapons_with_high_usage = [name.split('_')[0] for name in sum_weapon_usage.index[:17]]
weapons_with_high_usage

['ak-47',
 'assault',
 'pistol',
 'combat',
 'desert',
 'tactical',
 'military',
 'magnum',
 'katana',
 'silenced',
 'uzi',
 'fire',
 'chrome',
 'pump',
 'hunting',
 'chainsaw',
 'machete']

In [87]:
# separate these to a  dataframe
df_weapons = df[[col for col in df.columns if col.split('_')[0] in weapons_with_high_usage]]
df_weapons.head()

pistol_shots  pistol_kills  pistol_usage  magnum_shots  magnum_kills  \
0       94665.0       10470.0          2.77      121222.0       27056.0   
1        9136.0        1371.0          1.47       14928.0        6802.0   
2        4100.0         693.0          4.87         222.0         133.0   
3        7369.0        1208.0          5.99         784.0         250.0   
4       51944.0        9481.0          8.93       20545.0        6813.0   

   magnum_usage  uzi_shots  uzi_kills  uzi_usage  silenced_smg_shots  ...  \
0          7.16    44666.0     5165.0       1.37             57448.0  ...   
1          7.30      997.0      187.0       0.20              8497.0  ...   
2          0.93     2834.0      271.0       1.90              3298.0  ...   
3          1.24     3322.0      496.0       2.46              2805.0  ...   
4          6.42    38224.0     5493.0       5.17             36730.0  ...   

   chainsaw_usage  fire_axe_shots  fire_axe_kills  fire_axe_usage  \
0            1.10         67247.0         36781.0            9.73   
1            1.09          6187.0          7624.0            8.18   
2            2.65          2720.0          1187.0            8.34   
3            0.79           628.0           348.0            1.73   
4            0.38          6729.0          3909.0            3.68   

   katana_shots  katana_kills  katana_usage  machete_shots  machete_kills  \
0       46707.0       21434.0          5.67        36408.0        17608.0   
1        2223.0        2562.0          2.75         2572.0         2494.0   
2        1731.0         696.0          4.89          727.0          323.0   
3        1948.0        1116.0          5.54          919.0          538.0   
4        4024.0        2463.0          2.32         4646.0         2265.0   

   machete_usage  
0           4.66  
1           2.68  
2           2.27  
3           2.67  
4           2.13  

[5 rows x 51 columns]

In [88]:
# plotting the sum utility throws
sum_utility_usage = df[[col for col in df.columns if 'thrown' in col]].sum(axis=0).sort_values(ascending=False)
px.bar(sum_utility_usage).update_layout(
    xaxis_title='utility', yaxis_title='number of all uses', title='usage of different utilities')

We can see that out of the three utilities *bile_jar*s are used the least often, but they still have considerable usage, so we can consider them as well.

Any weapon's *shot*s and *kills* scale obviously with playtime; of course, since the more a user has played the total number of weapon shots and weapon kills should increase. Thus, these features should instead be converted to ratios e.g. kills/shots, which I will call the *rate* of a given weapon and utility. This extracted feature should be in connection with a player's skill. We suspect that a player gets more accurate and skillful the longer he/she plays. If we want to model how much a player has played baseon on their skill, we should use this extracted feature. Let's create a new dataframe that has the *usage*s and *rate*s of the weapons and utilities and also the meta features.

In [89]:
# we just divide the shots with the kills for each weapon
dict_rate_weapons = {f'{col.split("_shots")[0]}_rate': df_weapons[col.replace('shots', 'kills')]/df_weapons[col] for col in df_weapons.columns if '_shots' in col}
df_rate_weapons = pd.DataFrame.from_dict(dict_rate_weapons)

# division by zero here gives us nans, so we convert those indices to a 0 rate
df_rate_weapons.fillna(0, inplace=True)

df_rate_weapons.head(5)

pistol_rate  magnum_rate  uzi_rate  silenced_smg_rate  pump_shotgun_rate  \
0     0.110601     0.223194  0.115636           0.117706           0.531987   
1     0.150066     0.455654  0.187563           0.247028           0.715693   
2     0.169024     0.599099  0.095625           0.180412           0.816133   
3     0.163930     0.318878  0.149308           0.194296           0.601611   
4     0.182523     0.331614  0.143706           0.155214           0.565577   

   chrome_shotgun_rate  tactical_shotgun_rate  combat_shotgun_rate  \
0             0.548538               0.355437             0.375748   
1             0.781834               0.671355             0.679583   
2             0.691083               0.663611             0.694444   
3             0.538095               0.313346             0.391417   
4             0.532419               0.397363             0.413766   

   assault_rifle_rate  desert_rifle_rate  ak-47_rate  hunting_rifle_rate  \
0            0.169087           0.140979    0.235696            0.238004   
1            0.694371           0.286713    0.489695            0.533599   
2            0.158063           0.286818    0.231471            0.316667   
3            0.285340           0.295464    0.439602            0.367984   
4            0.211232           0.176446    0.283983            0.288631   

   military_sniper_rifle_rate  chainsaw_rate  fire_axe_rate  katana_rate  \
0                    0.231004       0.147046       0.546954     0.458903   
1                    0.475709       0.317188       1.232261     1.152497   
2                    0.363636       0.152817       0.436397     0.402080   
3                    0.478618       0.147465       0.554140     0.572895   
4                    0.310281       0.197368       0.580918     0.612078   

   machete_rate  
0      0.483630  
1      0.969673  
2      0.444292  
3      0.585419  
4      0.487516

In [90]:
# with the utilities we have to consider the slightly different naming conventions of the utility columns
df_utility = df[[col for col in df.columns if col.split('_')[0] in utility_names or col.split('_')[0]+'s' in utility_names]]
df_utility.rename(columns={col: col.replace('s_', '_').replace('_hits', '_kills') for col in df_utility.columns}, inplace=True)


# after this the rate can be calculated similarly
dict_rate_utility = {f'{col.split("_thrown")[0]}_rate': df_utility[col.replace('thrown', 'kills')]/df_utility[col] for col in df_utility.columns if '_thrown' in col}
df_rate_utility = pd.DataFrame.from_dict(dict_rate_utility)

# division by zero here gives us nans, so we convert those indices to a 0 rate
df_rate_utility.fillna(0, inplace=True)

df_rate_utility.head(5)

C:\Users\gyenist\AppData\Local\Temp\ipykernel_16532\2212541926.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



molotov_rate  pipe_bomb_rate  bile_jar_rate
0      8.891098        4.028365       2.216994
1     12.869289        7.125896       3.000000
2      5.652174        2.701124       1.886364
3      8.074074        6.819048       1.562500
4      7.825449        8.145631       1.558824

In [ ]:
# this can stay as it was
df_meta = df[meta_names]

In [91]:
# we can now concatenate the df-s to create our new dataframe with the extracted features
df = pd.concat([df_meta, df_rate_weapons, df_weapons[[c for c in df_weapons.columns if 'usage' in c]], df_rate_utility], axis=1)

# some more feature crossing
df['average_rate_weapon'] = df_rate_weapons.mean(axis=1)
df['average_rate_utility'] = df_rate_utility.mean(axis=1)
df['max_rate_weapon'] = df_rate_weapons.max(axis=1)
df['max_rate_utility'] = df_rate_utility.max(axis=1)

df.head()

username     playtime  difficulty  average_friendly_fire  pistol_rate  \
0         0  2433.577222           1                  142.0     0.110601   
1         1   121.879444           3                   89.0     0.150066   
2         2    69.955278           3                   58.0     0.169024   
3         3    48.421667           3                   76.0     0.163930   
4         4   307.639722           3                  112.0     0.182523   

   magnum_rate  uzi_rate  silenced_smg_rate  pump_shotgun_rate  \
0     0.223194  0.115636           0.117706           0.531987   
1     0.455654  0.187563           0.247028           0.715693   
2     0.599099  0.095625           0.180412           0.816133   
3     0.318878  0.149308           0.194296           0.601611   
4     0.331614  0.143706           0.155214           0.565577   

   chrome_shotgun_rate  ...  ak-47_usage  hunting_rifle_usage  \
0             0.548538  ...        12.46                 3.48   
1             0.781834  ...        14.31                 1.30   
2             0.691083  ...         5.88                 0.13   
3             0.538095  ...         8.11                 4.62   
4             0.532419  ...        10.53                 3.17   

   military_sniper_rifle_usage  chainsaw_usage  fire_axe_usage  katana_usage  \
0                         3.25            1.10            9.73          5.67   
1                         5.31            1.09            8.18          2.75   
2                         0.03            2.65            8.34          4.89   
3                        19.38            0.79            1.73          5.54   
4                         4.92            0.38            3.68          2.32   

   machete_usage  molotov_rate  pipe_bomb_rate  bile_jar_rate  
0           4.66      8.891098        4.028365       2.216994  
1           2.68     12.869289        7.125896       3.000000  
2           2.27      5.652174        2.701124       1.886364  
3           2.67      8.074074        6.819048       1.562500  
4           2.13      7.825449        8.145631       1.558824  

[5 rows x 41 columns]

## 3. Data Cleaning
With the newly extracted features we can inspect the dataset better and potentially clean it from some outliers and false records that could decrease model performance later.

Let's start by plotting some meta features.

In [92]:
px.scatter(x=df['username'], y=df['playtime']).update_layout(
    xaxis_title='username', yaxis_title='User Playtimes'
)

We can see some players with exceptionally high playtimes. Since playtime is measured in hours, playtime of 277k hr-s would be more than 30 years. 50k hr-s also seems a bit extreme, it being 5+ years of playtime. Let's remove these.

In [93]:
for _ in range(2):
    df = df[df['playtime'] != max(df['playtime'])]

In [95]:
px.scatter(x=df['username'], y=df['playtime'], trendline="ols", trendline_color_override='orange').update_layout(
    xaxis_title='username', yaxis_title='User Playtimes After Removing Extremes'
)